

## 1️⃣ What is Databricks? (Big Picture)

**Databricks = Management layer on top of Apache Spark**

* You **don’t manage Spark clusters manually**
* Databricks **creates, manages, scales, and secures Spark clusters** for you
* Works on **cloud storage** (Azure Data Lake, S3, GCS)

👉 Think of Databricks as **“Spark + Cloud + Governance + UI”**

---

## 2️⃣ Spark Cluster (Basic Concept)

**Spark Cluster = group of machines working together**

* **Driver node** → controls the job
* **Worker nodes** → execute tasks in parallel
* Used for **big data processing**

👉 Spark does computation
👉 Databricks manages Spark

---

## 3️⃣ Databricks Architecture (Very Important)

### Databricks has **TWO planes**

---

### 🟦 1. Control Plane (Databricks-managed)

**What it contains:**

* UI / UX (Notebooks, Jobs, SQL Editor)
* User management
* Cluster configuration
* Job scheduling
* Unity Catalog metadata
* Access control (permissions)

✅ **No customer data is stored here**

👉 This is the **brain**

---

### 🟩 2. Compute Plane (Customer cloud)

**What it contains:**

* Virtual Machines (VMs)
* Spark driver & workers
* Data processing
* Reads/writes data from cloud storage

👉 This is the **muscle**

---

### 🔁 Flow

```
User → UI (Control Plane)
        ↓
Spark Jobs → Compute Plane (VMs)
        ↓
Data → Cloud Storage (ADLS / S3)
```

---

## 4️⃣ Compute in Databricks (Azure-specific)

When you **create a cluster**:

* Databricks creates **VMs**
* These VMs are created in:
  👉 **Databricks-managed Resource Group**
* Spark runs on these VMs
* Data stays in **your Azure Data Lake**

📌 You **do not SSH into VMs**
📌 Databricks handles scaling & termination

---

## 5️⃣ WITHOUT Unity Catalog (Old Model)

![Image](https://docs.databricks.com/aws/en/assets/images/uc-catalogs-1a82cea378a5474ba080ebefc312cc12.png)

![Image](https://miro.medium.com/v2/resize%3Afit%3A1400/0%2AgmFjrEMdbX7KjlxA.png)

### Problems:

```
Workspace A → Metastore A
Workspace B → Metastore B
```

* Each workspace has **its own metastore**
* No central governance
* Hard to:
  ❌ Share data
  ❌ Manage permissions
  ❌ Track lineage
  ❌ Enforce security

👉 **Messy & unscalable**

---

## 6️⃣ WITH Unity Catalog (Modern Model)

![Image](https://docs.databricks.com/aws/en/assets/images/uc-catalogs-1a82cea378a5474ba080ebefc312cc12.png)

![Image](https://docs.databricks.com/aws/en/assets/images/managed-storage-0fe299ce1b4c32afce5845652093c124.png)

### Solution:

```
          Unity Catalog
     (Central Governance Layer)
              ↑
   Workspace A   Workspace B
```

### What Unity Catalog does:

* Central **metastore**
* Central **user & role management**
* Central **permissions**
* Central **data lineage & audit**

👉 **One governance layer for all workspaces**

---

## 7️⃣ What is Unity Catalog? (Simple Definition)

**Unity Catalog = Governance solution for Databricks**

It controls:

* Who can access what
* From which workspace
* On which data
* Stored in which cloud location

📌 It governs:

* Tables
* Views
* Volumes
* Functions
* External locations
* Credentials

---

## 8️⃣ Unity Catalog Object Model (Very Important)

![Image](https://docs.databricks.com/aws/en/assets/images/object-model-40d730065eefed283b936a8664f1b247.png)

![Image](https://docs.databricks.com/gcp/en/assets/images/object-hierarchy-fd5ca7071fad38082ad59f247fdd2410.png)

### 3-Level Namespace

```
catalog.schema.table
```

### Hierarchy Explained

```
Metastore
 └── Catalog
      └── Schema
           ├── Table
           ├── View
           ├── Volume
           └── Function
```

### Example

```sql
SELECT * FROM sales_catalog.finance.orders;
```

* `sales_catalog` → Catalog
* `finance` → Schema
* `orders` → Table

---

## 9️⃣ Unity Catalog – Extra Governance Objects

Unity Catalog also manages:

* **Storage Credential**
  → How Databricks authenticates to cloud storage

* **External Location**
  → Mapping of cloud path + credential

* **Service Credential**
  → Managed identity / service principal

👉 This is why **Unity Catalog is mandatory for external tables**

---

## 🔟 Final One-Line Summary (Interview Gold ⭐)

> **Databricks is a managed Spark platform where the control plane handles configuration and governance, the compute plane runs Spark on cloud VMs, and Unity Catalog provides centralized data governance across all workspaces using a three-level namespace (catalog.schema.object).**

---

2️⃣ Catalog

What it is:
A Catalog is a logical container for data objects.

Contains:

Schemas (databases)

Tables

Views

Functions

Purpose:
👉 Organize data + control access (governance)

Example:

sales_catalog

finance_catalog



### Managed Catalog-> Managed Schema->Managed Table

Catalog will use the location of Meta store

### Managed Catalog

In [0]:

%sql
CREATE CATALOG man_cata

### Managed Schema/Database

In [0]:
%sql
CREATE SCHEMA man_cata.man_schema

In [0]:
%sql

create table man_cata.man_schema.man_table(
  id int,
  name varchar(20)
)

using delta

### Scenario – 2

External Catalog – Managed Schema – Managed Table

In [0]:
%sql
CREATE CATALOG ext_cata
MANAGED LOCATION 'abfss://mycontainer@supermanstorage.dfs.core.windows.net/external_catalog'


In [0]:
%sql
CREATE SCHEMA ext_cata.man_schema


In [0]:
%sql
CREATE TABLE ext_cata.man_schema.man_table
(
    id INT,
    name STRING
)
USING DELTA
--- this time it will create the table in our storage container

### Scenario – 3

External Catalog – External Schema – Managed Table

In [0]:
%sql
CREATE SCHEMA ext_cata.ext_schema
MANAGED LOCATION 'abfss://mycontainer@supermanstorage.dfs.core.windows.net/ext_schema'


In [0]:
%sql
CREATE TABLE ext_cata.ext_schema.man_table3
(
    id INT,
    name STRING
)
USING DELTA


### Scenario – 4
Managed Catalog – Managed Schema – External Table

In [0]:
%sql
CREATE TABLE man_cata.man_schema.ext_table5
(
    id INT,
    name STRING
)
USING DELTA

LOCATION 'abfss://mycontainer@supermanstorage.dfs.core.windows.net/ext_table5'


### Drop managed table

In [0]:
%sql

drop table man_cata.man_schema.man_table;

--- it will detele the table after 7 days from the storage account if u are using unity catalog

---------------------------------------------------------------------------
AnalysisException                         Traceback (most recent call last)
File <command-7174274585283111>, line 1
----> 1 get_ipython().run_cell_magic('sql', '', '\ndrop table man_cata.man_schema.man_table;\n\n--- it will detele the table after 7 days from the storage account if u are using unity catalog\n')

File /databricks/python/lib/python3.12/site-packages/IPython/core/interactiveshell.py:2541, in InteractiveShell.run_cell_magic(self, magic_name, line, cell)
   2539 with self.builtin_trap:
   2540     args = (magic_arg_s, cell)
-> 2541     result = fn(*args, **kwargs)
   2543 # The code below prevents the output from being displayed
   2544 # when using magics with decorator @output_can_be_silenced
   2545 # when the last Python token in the expression is a ';'.
   2546 if getattr(fn, magic.MAGIC_OUTPUT_CAN_BE_SILENCED, False):

File /databricks/python_shell/lib/dbruntime/sql_magic/sql_magic.py:194, in S

### undrop managed table

In [0]:
%sql

undrop table man_cata.man_schema.man_table;


(Think in terms of **metadata** vs **actual data files**)

---

## First, simple rules to remember 🧠

* **Managed Table**
  👉 Databricks **manages data + metadata**
  👉 `DROP TABLE` = **data deleted + metadata deleted**

* **External Table**
  👉 Databricks manages **only metadata**
  👉 Data lives in **external storage (ADLS/S3)**
  👉 `DROP TABLE` = **metadata deleted, data stays**

* **Managed Schema**
  👉 Databricks controls storage location

* **External Schema**
  👉 Storage location is user-defined

---

## Scenario 1

### Managed Catalog → Managed Schema → Managed Table

📦 **Everything is fully managed by Databricks**

**When you DROP the table:**

* ❌ Metadata deleted
* ❌ Data files deleted from storage

✅ **Result:**
👉 **Table + data are completely gone**

---

## Scenario 2

### External Catalog → Managed Schema → Managed Table

📦 Catalog is external, but table is **managed**

**When you DROP the table:**

* ❌ Metadata deleted
* ❌ Data files deleted

✅ **Result:**
👉 **Same behavior as Scenario 1**
👉 **Data is deleted**

📌 Catalog type does NOT matter for managed tables

---

## Scenario 3

### External Catalog → External Schema → Managed Table

📦 Storage location is external, but table is **managed**

**When you DROP the table:**

* ❌ Metadata deleted
* ❌ Data files deleted

✅ **Result:**
👉 **Data is still deleted**

📌 **Managed table = Databricks owns lifecycle**

---

## Scenario 4

### Managed Catalog → Managed Schema → External Table

📦 Table data is stored **outside Databricks control**

**When you DROP the table:**

* ❌ Metadata deleted
* ✅ Data files remain in ADLS/S3

✅ **Result:**
👉 Table disappears
👉 **Data is still present in storage**

---

## One-line Summary Table 🧾

| Scenario | Table Type | DROP TABLE Result   |
| -------- | ---------- | ------------------- |
| 1        | Managed    | ❌ Metadata + ❌ Data |
| 2        | Managed    | ❌ Metadata + ❌ Data |
| 3        | Managed    | ❌ Metadata + ❌ Data |
| 4        | External   | ❌ Metadata only     |

---

## Golden Rule ⭐

> **Only table type matters — not catalog or schema**

* **Managed Table → Data deleted**
* **External Table → Data safe**

---

A Metastore is a central place that stores information about data, not the data itself.

It stores:

Which catalogs, schemas, tables exist

Table structure (columns, data types)

Permissions (who can access what)



### Qurying files using select


In [0]:
%sql
insert into man_cata.man_schema.ext_table5 values (1,"Yash"),(2,"Pop"),(3,"kol");

num_affected_rows num_inserted_rows 3 3

In [0]:
%sql
select * from man_cata.man_schema.ext_table5;

id name 1 Yash 2 Pop 3 kol

In [0]:
%sql
select * from delta.`abfss://mycontainer@supermanstorage.dfs.core.windows.net/ext_table5`

id name 1 Yash 2 Pop 3 kol

### Temporary View vs Permanent View


| Temporary View                               | Permanent View                      |
| -------------------------------------------- | ----------------------------------- |
| Created for **current session/cluster**      | Stored **permanently** in metastore |
| Exists only while **cluster is running**     | Exists even after cluster stops     |
| Deleted when **cluster is detached/stopped** | **Not deleted** when cluster stops  |
| Not shared with other clusters               | Can be used by **any cluster**      |
| No metadata saved permanently                | Metadata saved in **metastore**     |




In [0]:
%sql
create view man_cata.man_schema.view1 as
select * from delta.`abfss://mycontainer@supermanstorage.dfs.core.windows.net/ext_table5` where id =1;

In [0]:
%sql
select * from man_cata.man_schema.view1;

id name 1 Yash

### Temporary view


In [0]:
%sql

create or replace temp view view2 as
select * from delta.`abfss://mycontainer@supermanstorage.dfs.core.windows.net/ext_table5` where id =2;

In [0]:
%sql
select * from view2;

id name 2 Pop

In [0]:
print("hello")

hello


In [0]:
#Flatten json data

from pyspark.sql.functions import *
dbutils.fs.ls("abfss://mycontainer@supermanstorage.dfs.core.windows.net/")

df=spark.read.format("json")\
    .option("multiline",True)\
    .load("abfss://mycontainer@supermanstorage.dfs.core.windows.net/1mb.json")
df.display()


address email name phone website 81323 Simone Flats Apt. 695
South Lucileville, CO 24991 katherine60@hotmail.com Ms. Autumn Skiles +1 (648) 391-8320 https://examplefile.com 13859 Pasquale Mountain Suite 734
South Dayneview, WA 27288 kboyer@reichert.info Mrs. Reba Heathcote 619.230.2594 https://examplefile.com 461 Hand Rapid
Lake Angeloville, KS 45943 dbrown@hotmail.com Prof. Dale Schiller IV (830) 797-0870 x597 https://examplefile.com 2182 Brown Route Suite 918
Mariebury, ID 83868 joanie.toy@hackett.com Miss Leonie Dach (753) 618-9594 x983 https://examplefile.com 762 Powlowski Prairie
Lake Hopestad, WV 47233-0316 wendy.zieme@yahoo.com Ruth Stiedemann (221) 299-7141 x80069 https://examplefile.com 989 Streich Hill Suite 443
North Rupert, HI 15392-1702 melody.collier@gmail.com Gunnar Ankunding PhD 419.829.8089 x93032 https://examplefile.com 570 Mraz Passage Suite 168
North Jalenhaven, WI 05266 yharvey@hotmail.com Mrs. Ilene Bosco +1 (721) 446-8287 https://examplefile.com 342 McKenzie Stream Apt. 723
Schowalterchester, AR 24179 kathleen.homenick@hotmail.com Dr. Benedict Cole DVM 1-462-704-4464 https://examplefile.com 89593 Augusta Fork
Lizethmouth, DE 29401 carmen16@torp.com Loraine Rodriguez 467-386-3544 x5693 https://examplefile.com 8861 Chanel Valley Suite 842
Waltershire, NH 10354 conn.milford@gmail.com Cleta Mann +18628329942 https://examplefile.com 256 West Alley Apt. 582
Port Austen, AZ 60293-3774 howard.kilback@wiegand.com Janiya Reinger 1-649-626-3712 x7366 https://examplefile.com 14448 Kozey Path Suite 536
Littleland, GA 92027 haag.diana@boyle.com Dr. Bethel Kessler (928) 973-3797 https://examplefile.com 865 Alberta Haven
South Vitotown, CO 91336-1697 alanis41@gmail.com Dr. Hyman Haley DDS +1.639.347.3128 https://examplefile.com 931 Daisy Crescent Suite 725
South Briana, NE 51869 jenkins.nova@kertzmann.net Desiree Mertz +15418171247 https://examplefile.com 31749 Jaclyn Gardens
South Waynechester, TX 20369 jerrell07@lemke.com Jairo Effertz DDS 827-435-3987 x32728 https://examplefile.com 3053 Lubowitz Glens Apt. 454
West Amanda, MA 96331-8734 karl03@gmail.com Ms. Nedra Corkery 752.869.1280 https://examplefile.com 57854 General Extension
Mazieport, IA 44210-7793 jaskolski.rosemary@gmail.com Barrett Treutel 723-692-9235 https://examplefile.com 41720 Thiel Port
Jastville, WV 66557 bgulgowski@cormier.com Jettie Schmitt 1-805-361-7424 x5224 https://examplefile.com 55508 Berge Isle Suite 939
Crooksmouth, OK 33262 hwunsch@conroy.org Penelope Mueller 571-749-8851 x1515 https://examplefile.com 48781 Teresa Mills Suite 177
West Fausto, NH 01864 santa14@yahoo.com Dr. Sim Halvorson 956.393.5445 https://examplefile.com 19439 Howard Crest Suite 257
South Eloisa, OH 76395-4708 tbins@hotmail.com Gustave Green 1-357-265-0840 https://examplefile.com 69143 Davis Forks
Schadenstad, FL 76333-4633 micheal39@hotmail.com Leland King +1.906.702.8818 https://examplefile.com 6033 O'Kon Manor
Denesikborough, WV 16998 roberto.schuster@waters.com Prof. Monte Hartmann DDS 1-623-985-0621 https://examplefile.com 696 Lesley Row Apt. 103
North Paulmouth, HI 77882 jroberts@breitenberg.com Enrique Smith 1-415-207-3780 x8266 https://examplefile.com 8309 Pfeffer Islands Apt. 864
Schmelerview, KS 46540-3074 uborer@yahoo.com Mrs. Brandy Mann (393) 784-0128 x385 https://examplefile.com 61414 Kilback Dale
Lorenzborough, WA 17085-7455 mayer.felicity@bednar.biz Miss Reina McGlynn 1-834-820-1281 https://examplefile.com 6487 Kozey Green Suite 370
North Juniusview, IL 99696-1888 vonrueden.karelle@stehr.biz Miss Aubrey Crona 465.296.9569 x876 https://examplefile.com 8741 Nayeli Village Suite 274
New Richmond, NH 47877-2123 brielle09@gmail.com Houston Lebsack 1-507-992-8158 https://examplefile.com 4388 Cyril Valleys Apt. 951
Herzogmouth, MT 00376 reta28@reilly.com Santa Morar 373-860-7103 x4986 https://examplefile.com 8024 Christiansen Park
North Idabury, CT 52740 schuyler49@skiles.biz Valentin Flatley +12719525748 https://examplefile.com 84786 Claud Stravenue Apt. 105
La

### Json data flatning

In [0]:
json_sample = """{
  "id": "0001",
  "type": "donut",
  "name": "Cake",
  "ppu": 0.55,
  "batters": {
    "batter": [
      { "id": "1001", "type": "Regular" },
      { "id": "1002", "type": "Chocolate" },
      { "id": "1003", "type": "Blueberry" },
      { "id": "1004", "type": "Devil's Food" }
    ]
  },
  "topping": [
    { "id": "5001", "type": "None" },
    { "id": "5002", "type": "Glazed" },
    { "id": "5005", "type": "Sugar" },
    { "id": "5007", "type": "Powdered Sugar" },
    { "id": "5006", "type": "Chocolate with Sprinkles" },
    { "id": "5003", "type": "Chocolate" },
    { "id": "5004", "type": "Maple" }
  ]
}"""


dbutils.fs.put(
  "abfss://mycontainer@supermanstorage.dfs.core.windows.net/json/donut.json",
  json_sample,
  True
)



Wrote 616 bytes.


True

In [0]:
df=spark.read.format("json")\
    .option("multiline",True)\
    .load("abfss://mycontainer@supermanstorage.dfs.core.windows.net/json/donut.json")
df.display()

batters id name ppu topping type List(List(List(1001, Regular), List(1002, Chocolate), List(1003, Blueberry), List(1004, Devil's Food))) 0001 Cake 0.55 List(List(5001, None), List(5002, Glazed), List(5005, Sugar), List(5007, Powdered Sugar), List(5006, Chocolate with Sprinkles), List(5003, Chocolate), List(5004, Maple)) donut

In [0]:
df.printSchema()

root
 |-- batters: struct (nullable = true)
 |    |-- batter: array (nullable = true)
 |    |    |-- element: struct (containsNull = true)
 |    |    |    |-- id: string (nullable = true)
 |    |    |    |-- type: string (nullable = true)
 |-- id: string (nullable = true)
 |-- name: string (nullable = true)
 |-- ppu: double (nullable = true)
 |-- topping: array (nullable = true)
 |    |-- element: struct (containsNull = true)
 |    |    |-- id: string (nullable = true)
 |    |    |-- type: string (nullable = true)
 |-- type: string (nullable = true)



In [0]:
df_final=df.withColumn("new_batters",explode("batters.batter"))
display(df_final)

batters id name ppu topping type new_batters List(List(List(1001, Regular), List(1002, Chocolate), List(1003, Blueberry), List(1004, Devil's Food))) 0001 Cake 0.55 List(List(5001, None), List(5002, Glazed), List(5005, Sugar), List(5007, Powdered Sugar), List(5006, Chocolate with Sprinkles), List(5003, Chocolate), List(5004, Maple)) donut List(1001, Regular) List(List(List(1001, Regular), List(1002, Chocolate), List(1003, Blueberry), List(1004, Devil's Food))) 0001 Cake 0.55 List(List(5001, None), List(5002, Glazed), List(5005, Sugar), List(5007, Powdered Sugar), List(5006, Chocolate with Sprinkles), List(5003, Chocolate), List(5004, Maple)) donut List(1002, Chocolate) List(List(List(1001, Regular), List(1002, Chocolate), List(1003, Blueberry), List(1004, Devil's Food))) 0001 Cake 0.55 List(List(5001, None), List(5002, Glazed), List(5005, Sugar), List(5007, Powdered Sugar), List(5006, Chocolate with Sprinkles), List(5003, Chocolate), List(5004, Maple)) donut List(1003, Blueberry) List(List(List(1001, Regular), List(1002, Chocolate), List(1003, Blueberry), List(1004, Devil's Food))) 0001 Cake 0.55 List(List(5001, None), List(5002, Glazed), List(5005, Sugar), List(5007, Powdered Sugar), List(5006, Chocolate with Sprinkles), List(5003, Chocolate), List(5004, Maple)) donut List(1004, Devil's Food)

In [0]:
flattenDF=df.withColumn("new_batters",explode("batters.batter"))\
    .withColumn("new_topping",explode("topping"))\
    .drop("batters","topping")
display(flattenDF)

id name ppu type new_batters new_topping 0001 Cake 0.55 donut List(1001, Regular) List(5001, None) 0001 Cake 0.55 donut List(1001, Regular) List(5002, Glazed) 0001 Cake 0.55 donut List(1001, Regular) List(5005, Sugar) 0001 Cake 0.55 donut List(1001, Regular) List(5007, Powdered Sugar) 0001 Cake 0.55 donut List(1001, Regular) List(5006, Chocolate with Sprinkles) 0001 Cake 0.55 donut List(1001, Regular) List(5003, Chocolate) 0001 Cake 0.55 donut List(1001, Regular) List(5004, Maple) 0001 Cake 0.55 donut List(1002, Chocolate) List(5001, None) 0001 Cake 0.55 donut List(1002, Chocolate) List(5002, Glazed) 0001 Cake 0.55 donut List(1002, Chocolate) List(5005, Sugar) 0001 Cake 0.55 donut List(1002, Chocolate) List(5007, Powdered Sugar) 0001 Cake 0.55 donut List(1002, Chocolate) List(5006, Chocolate with Sprinkles) 0001 Cake 0.55 donut List(1002, Chocolate) List(5003, Chocolate) 0001 Cake 0.55 donut List(1002, Chocolate) List(5004, Maple) 0001 Cake 0.55 donut List(1003, Blueberry) List(5001, None) 0001 Cake 0.55 donut List(1003, Blueberry) List(5002, Glazed) 0001 Cake 0.55 donut List(1003, Blueberry) List(5005, Sugar) 0001 Cake 0.55 donut List(1003, Blueberry) List(5007, Powdered Sugar) 0001 Cake 0.55 donut List(1003, Blueberry) List(5006, Chocolate with Sprinkles) 0001 Cake 0.55 donut List(1003, Blueberry) List(5003, Chocolate) 0001 Cake 0.55 donut List(1003, Blueberry) List(5004, Maple) 0001 Cake 0.55 donut List(1004, Devil's Food) List(5001, None) 0001 Cake 0.55 donut List(1004, Devil's Food) List(5002, Glazed) 0001 Cake 0.55 donut List(1004, Devil's Food) List(5005, Sugar) 0001 Cake 0.55 donut List(1004, Devil's Food) List(5007, Powdered Sugar) 0001 Cake 0.55 donut List(1004, Devil's Food) List(5006, Chocolate with Sprinkles) 0001 Cake 0.55 donut List(1004, Devil's Food) List(5003, Chocolate) 0001 Cake 0.55 donut List(1004, Devil's Food) List(5004, Maple)

In [0]:


flattenDF = flattenDF.select(
    col("id"),
    col("name"),
    col("ppu"),
    col("type"),
    col("new_batters.id").alias("batter_id"),
    col("new_batters.type").alias("batter_type"),
    col("new_topping.id").alias("topping_id"),
    col("new_topping.type").alias("topping_type")
)
display(flattenDF)

id name ppu type batter_id batter_type topping_id topping_type 0001 Cake 0.55 donut 1001 Regular 5001 None 0001 Cake 0.55 donut 1001 Regular 5002 Glazed 0001 Cake 0.55 donut 1001 Regular 5005 Sugar 0001 Cake 0.55 donut 1001 Regular 5007 Powdered Sugar 0001 Cake 0.55 donut 1001 Regular 5006 Chocolate with Sprinkles 0001 Cake 0.55 donut 1001 Regular 5003 Chocolate 0001 Cake 0.55 donut 1001 Regular 5004 Maple 0001 Cake 0.55 donut 1002 Chocolate 5001 None 0001 Cake 0.55 donut 1002 Chocolate 5002 Glazed 0001 Cake 0.55 donut 1002 Chocolate 5005 Sugar 0001 Cake 0.55 donut 1002 Chocolate 5007 Powdered Sugar 0001 Cake 0.55 donut 1002 Chocolate 5006 Chocolate with Sprinkles 0001 Cake 0.55 donut 1002 Chocolate 5003 Chocolate 0001 Cake 0.55 donut 1002 Chocolate 5004 Maple 0001 Cake 0.55 donut 1003 Blueberry 5001 None 0001 Cake 0.55 donut 1003 Blueberry 5002 Glazed 0001 Cake 0.55 donut 1003 Blueberry 5005 Sugar 0001 Cake 0.55 donut 1003 Blueberry 5007 Powdered Sugar 0001 Cake 0.55 donut 1003 Blueberry 5006 Chocolate with Sprinkles 0001 Cake 0.55 donut 1003 Blueberry 5003 Chocolate 0001 Cake 0.55 donut 1003 Blueberry 5004 Maple 0001 Cake 0.55 donut 1004 Devil's Food 5001 None 0001 Cake 0.55 donut 1004 Devil's Food 5002 Glazed 0001 Cake 0.55 donut 1004 Devil's Food 5005 Sugar 0001 Cake 0.55 donut 1004 Devil's Food 5007 Powdered Sugar 0001 Cake 0.55 donut 1004 Devil's Food 5006 Chocolate with Sprinkles 0001 Cake 0.55 donut 1004 Devil's Food 5003 Chocolate 0001 Cake 0.55 donut 1004 Devil's Food 5004 Maple

In [0]:
# only one partintion csv file save to storage acc
flattenDF.coalesce(1) \
    .write \
    .mode("overwrite") \
    .option("header", "true") \
    .csv("abfss://mycontainer@supermanstorage.dfs.core.windows.net/flattenfile")


### Volumes


> **Volumes** are used to store **files (not tables)** in Databricks.

#### What you store in Volumes:

* CSV, JSON, Parquet files
* Images, PDFs, logs
* ML models, checkpoints

#### Key points:

* Managed by **Unity Catalog**
* Accessed like a **folder**
* Supports permissions (READ / WRITE)

#### Example path:

```
/Volumes/sales_catalog/raw_schema/input_files/
```

🧠 **Easy line:**

> Volumes are secure folders in Databricks for storing and accessing files instead of tables.


In [0]:
#creating a dir for volume

dbutils.fs.mkdirs("abfss://mycontainer@supermanstorage.dfs.core.windows.net/volumes")

True

Creating a volume


In [0]:
%sql

create external volume man_cata.man_schema.myvolumeext
location "abfss://mycontainer@supermanstorage.dfs.core.windows.net/volumes"

### Copy file for volume

In [0]:
dbutils.fs.cp(
  "abfss://mycontainer@supermanstorage.dfs.core.windows.net/source/",
  "abfss://mycontainer@supermanstorage.dfs.core.windows.net/volumes/business"
, recurse=True)


True

### Query the volume

In [0]:
%sql

select * from csv.`/Volumes/man_cata/man_schema/myvolumeext/business/business-financial-data-september-2025-quarter.csv`

_c0 _c1 _c2 _c3 _c4 _c5 _c6 _c7 _c8 _c9 _c10 _c11 _c12 _c13 Series_reference Period Data_value Suppressed STATUS UNITS Magnitude Subject Group Series_title_1 Series_title_2 Series_title_3 Series_title_4 Series_title_5 BDCQ.SF1AA2CA 2016.06 1116.386 null F Dollars 6 Business Data Collection - BDC Industry by financial variable (NZSIOC Level 2) Sales (operating income) Forestry and Logging Current prices Unadjusted null BDCQ.SF1AA2CA 2016.09 1070.874 null F Dollars 6 Business Data Collection - BDC Industry by financial variable (NZSIOC Level 2) Sales (operating income) Forestry and Logging Current prices Unadjusted null BDCQ.SF1AA2CA 2016.12 1054.408 null F Dollars 6 Business Data Collection - BDC Industry by financial variable (NZSIOC Level 2) Sales (operating income) Forestry and Logging Current prices Unadjusted null BDCQ.SF1AA2CA 2017.03 1010.665 null F Dollars 6 Business Data Collection - BDC Industry by financial variable (NZSIOC Level 2) Sales (operating income) Forestry and Logging Current prices Unadjusted null BDCQ.SF1AA2CA 2017.06 1233.7 null F Dollars 6 Business Data Collection - BDC Industry by financial variable (NZSIOC Level 2) Sales (operating income) Forestry and Logging Current prices Unadjusted null BDCQ.SF1AA2CA 2017.09 1282.436 null F Dollars 6 Business Data Collection - BDC Industry by financial variable (NZSIOC Level 2) Sales (operating income) Forestry and Logging Current prices Unadjusted null BDCQ.SF1AA2CA 2017.12 1290.82 null F Dollars 6 Business Data Collection - BDC Industry by financial variable (NZSIOC Level 2) Sales (operating income) Forestry and Logging Current prices Unadjusted null BDCQ.SF1AA2CA 2018.03 1412.007 null F Dollars 6 Business Data Collection - BDC Industry by financial variable (NZSIOC Level 2) Sales (operating income) Forestry and Logging Current prices Unadjusted null BDCQ.SF1AA2CA 2018.06 1488.055 null F Dollars 6 Business Data Collection - BDC Industry by financial variable (NZSIOC Level 2) Sales (operating income) Forestry and Logging Current prices Unadjusted null BDCQ.SF1AA2CA 2018.09 1497.678 null F Dollars 6 Business Data Collection - BDC Industry by financial variable (NZSIOC Level 2) Sales (operating income) Forestry and Logging Current prices Unadjusted null BDCQ.SF1AA2CA 2018.12 1570.507 null F Dollars 6 Business Data Collection - BDC Industry by financial variable (NZSIOC Level 2) Sales (operating income) Forestry and Logging Current prices Unadjusted null BDCQ.SF1AA2CA 2019.03 1393.749 null F Dollars 6 Business Data Collection - BDC Industry by financial variable (NZSIOC Level 2) Sales (operating income) Forestry and Logging Current prices Unadjusted null BDCQ.SF1AA2CA 2019.06 1517.143 null F Dollars 6 Business Data Collection - BDC Industry by financial variable (NZSIOC Level 2) Sales (operating income) Forestry and Logging Current prices Unadjusted null BDCQ.SF1AA2CA 2019.09 1381.514 null F Dollars 6 Business Data Collection - BDC Industry by financial variable (NZSIOC Level 2) Sales (operating income) Forestry and Logging Current prices Unadjusted null BDCQ.SF1AA2CA 2019.12 1370.985 null F Dollars 6 Business Data Collection - BDC Industry by financial variable (NZSIOC Level 2) Sales (operating income) Forestry and Logging Current prices Unadjusted null BDCQ.SF1AA2CA 2020.03 1073.017 null F Dollars 6 Business Data Collection - BDC Industry by financial variable (NZSIOC Level 2) Sales (operating income) Forestry and Logging Current prices Unadjusted null BDCQ.SF1AA2CA 2020.06 1131.445 null F Dollars 6 Business Data Collection - BDC Industry by financial variable (NZSIOC Level 2) Sales (operating income) Forestry and Logging Current prices Unadjusted null BDCQ.SF1AA2CA 2020.09 1440.101 null F Dollars 6 Business Data Collection - BDC Industry by financial variable (NZSIOC Level 2) Sales (operating income) Forestry and Logging Current prices Unadjusted null BDCQ.SF1AA2CA 2020.12 1489.979 null F Dollars 6 Business Data Collection - BDC Industry by financial variable (NZ

### Delta Lake

### Delta table

In [0]:
%sql

create table man_cata.man_schema.deltatable
(
  id int,
  name string,
  city string
)

using delta 
location "abfss://mycontainer@supermanstorage.dfs.core.windows.net/deltalake/deltatable"

### Turn off deletion vector

In [0]:
%sql
alter table man_cata.man_schema.deltatable set tblproperties ("delta.enableDeletionVectors"=false);

In [0]:
%sql

insert into man_cata.man_schema.deltatable values
(1,"aa","Delhi"),(2,"bb","londom"),(3,"cc","sydney");

num_affected_rows num_inserted_rows 3 3

In [0]:
%sql

describe extended man_cata.man_schema.deltatable;

col_name data_type comment id int null name string null city string null # Delta Statistics Columns Column Names id, name, city Column Selection Method first-32 # Detailed Table Information Catalog man_cata Database man_schema Table deltatable Created Time Wed Jan 07 13:21:11 UTC 2026 Last Access UNKNOWN Created By Spark Type EXTERNAL Collation UTF8_BINARY Location abfss://mycontainer@supermanstorage.dfs.core.windows.net/deltalake/deltatable Provider delta Owner yashthunder12345@gmail.com Table Properties [delta.enableDeletionVectors=false,delta.feature.appendOnly=supported,delta.feature.deletionVectors=supported,delta.feature.invariants=supported,delta.minReaderVersion=3,delta.minWriterVersion=7,delta.writePartitionColumnsToParquet=true]

In [0]:
%sql 
select * from man_cata.man_schema.deltatable;

id name city 1 aa Delhi 2 bb londom 3 cc sydney

### CRUD 

### update in delta table 

In [0]:
%sql

update man_cata.man_schema.deltatable set city ="toruno" where id =1;


--prev file will get tombstoned


num_affected_rows 1

### versioning

In [0]:
%sql

describe history man_cata.man_schema.deltatable;

version timestamp userId userName operation operationParameters job notebook clusterId readVersion isolationLevel isBlindAppend operationMetrics userMetadata engineInfo 4 2026-01-08T04:24:25.000Z 142155304183077 yashthunder12345@gmail.com UPDATE Map(predicate -> ["(id#13462 = 1)"]) null List(2196879026769418) 0108-041546-i91px7bt-v2n 3 WriteSerializable false Map(numRemovedFiles -> 1, numRemovedBytes -> 1017, numCopiedRows -> 2, numDeletionVectorsAdded -> 0, numDeletionVectorsRemoved -> 0, numAddedChangeFiles -> 0, executionTimeMs -> 915, numDeletionVectorsUpdated -> 0, scanTimeMs -> 259, numAddedFiles -> 1, numUpdatedRows -> 1, numAddedBytes -> 1017, rewriteTimeMs -> 656) null Databricks-Runtime/17.3.x-photon-scala2.13 3 2026-01-08T04:21:57.000Z 142155304183077 yashthunder12345@gmail.com UPDATE Map(predicate -> ["(id#13345 = 1)"]) null List(2196879026769418) 0108-041546-i91px7bt-v2n 2 WriteSerializable false Map(numRemovedFiles -> 1, numRemovedBytes -> 1000, numCopiedRows -> 2, numDeletionVectorsAdded -> 0, numDeletionVectorsRemoved -> 0, numAddedChangeFiles -> 0, executionTimeMs -> 1228, numDeletionVectorsUpdated -> 0, scanTimeMs -> 342, numAddedFiles -> 1, numUpdatedRows -> 1, numAddedBytes -> 1017, rewriteTimeMs -> 876) null Databricks-Runtime/17.3.x-photon-scala2.13 2 2026-01-07T13:26:43.000Z 142155304183077 yashthunder12345@gmail.com WRITE Map(mode -> Append, statsOnLoad -> false, partitionBy -> []) null List(2196879026769418) 0107-131359-sdk97266-v2n 1 WriteSerializable true Map(numFiles -> 1, numOutputRows -> 3, numOutputBytes -> 1000) null Databricks-Runtime/17.3.x-photon-scala2.13 1 2026-01-07T13:23:51.000Z 142155304183077 yashthunder12345@gmail.com SET TBLPROPERTIES Map(properties -> {"delta.enableDeletionVectors":"false"}) null List(2196879026769418) 0107-131359-sdk97266-v2n 0 WriteSerializable true Map() null Databricks-Runtime/17.3.x-photon-scala2.13 0 2026-01-07T13:21:10.000Z 142155304183077 yashthunder12345@gmail.com CREATE TABLE Map(partitionBy -> [], clusterBy -> [], description -> null, isManaged -> false, properties -> {"delta.enableDeletionVectors":"true","delta.writePartitionColumnsToParquet":"true"}, statsOnLoad -> false) null List(2196879026769418) 0107-131359-sdk97266-v2n null WriteSerializable true Map() null Databricks-Runtime/17.3.x-photon-scala2.13

### Time travel

In [0]:
%sql
restore man_cata.man_schema.deltatable to version as of 2

table_size_after_restore num_of_files_after_restore num_removed_files num_restored_files removed_files_size restored_files_size 1000 1 1 1 1017 1000

In [0]:
%sql

select * from man_cata.man_schema.deltatable;

id name city 1 aa Delhi 2 bb londom 3 cc sydney


### deletion vector

In [0]:
%sql

create table man_cata.man_schema.deltatable2
(
  id int,
  name string,
  city string
)

using delta 
location "abfss://mycontainer@supermanstorage.dfs.core.windows.net/deltalake/deltatable2"

In [0]:
%sql

insert into man_cata.man_schema.deltatable2 values
(1,"aa","Delhi"),(2,"bb","londom"),(3,"cc","sydney");

num_affected_rows num_inserted_rows 3 3

### Update in Deletion Vector Table

When **Deletion Vectors** are enabled on a Delta table,  
**UPDATE** and **DELETE** operations do **not rewrite the entire data files**.

Instead:
- Deleted rows are marked using **deletion vectors**
- This makes updates and deletes **faster**
- The table avoids heavy file rewrites

⚠️ **Important:**  
Deletion Vectors **do NOT automatically run OPTIMIZE**.

- **OPTIMIZE** is still required to:
  - Combine many small files into larger files
  - Improve query performance

✅ **Summary:**  
Deletion vectors speed up updates and deletes,  
but **OPTIMIZE must be run separately** to improve read performance.
```


In [0]:
%sql

update man_cata.man_schema.deltatable2
set city='seatal' where id =1;


num_affected_rows 1

### Optimize in delta table


In [0]:
%sql

describe history man_cata.man_schema.deltatable2;

version timestamp userId userName operation operationParameters job notebook clusterId readVersion isolationLevel isBlindAppend operationMetrics userMetadata engineInfo 3 2026-01-08T04:31:54.000Z 142155304183077 yashthunder12345@gmail.com OPTIMIZE Map(predicate -> [], auto -> true, clusterBy -> [], zOrderBy -> [], batchId -> 0) null List(2196879026769418) 0108-041546-i91px7bt-v2n 2 SnapshotIsolation false Map(numRemovedFiles -> 2, numRemovedBytes -> 1979, p25FileSize -> 1019, numDeletionVectorsRemoved -> 1, minFileSize -> 1019, numAddedFiles -> 1, maxFileSize -> 1019, p75FileSize -> 1019, p50FileSize -> 1019, numAddedBytes -> 1019) null Databricks-Runtime/17.3.x-photon-scala2.13 2 2026-01-08T04:31:52.000Z 142155304183077 yashthunder12345@gmail.com UPDATE Map(predicate -> ["(id#15037 = 1)"]) null List(2196879026769418) 0108-041546-i91px7bt-v2n 1 WriteSerializable false Map(numRemovedFiles -> 0, numRemovedBytes -> 0, numCopiedRows -> 0, numDeletionVectorsAdded -> 1, numDeletionVectorsRemoved -> 0, numAddedChangeFiles -> 0, executionTimeMs -> 2145, numDeletionVectorsUpdated -> 0, scanTimeMs -> 1198, numAddedFiles -> 1, numUpdatedRows -> 1, numAddedBytes -> 979, rewriteTimeMs -> 937) null Databricks-Runtime/17.3.x-photon-scala2.13 1 2026-01-08T04:30:08.000Z 142155304183077 yashthunder12345@gmail.com WRITE Map(mode -> Append, statsOnLoad -> false, partitionBy -> []) null List(2196879026769418) 0108-041546-i91px7bt-v2n 0 WriteSerializable true Map(numFiles -> 1, numOutputRows -> 3, numOutputBytes -> 1000) null Databricks-Runtime/17.3.x-photon-scala2.13 0 2026-01-08T04:29:28.000Z 142155304183077 yashthunder12345@gmail.com CREATE TABLE Map(partitionBy -> [], clusterBy -> [], description -> null, isManaged -> false, properties -> {"delta.enableDeletionVectors":"true","delta.writePartitionColumnsToParquet":"true"}, statsOnLoad -> false) null List(2196879026769418) 0108-041546-i91px7bt-v2n null WriteSerializable true Map() null Databricks-Runtime/17.3.x-photon-scala2.13

In [0]:
%sql

optimize man_cata.man_schema.deltatable2;

path metrics abfss://mycontainer@supermanstorage.dfs.core.windows.net/deltalake/deltatable2 List(0, 0, List(null, null, 0.0, 0, 0), List(null, null, 0.0, 0, 0), 0, null, null, 0, 0, 1, 1, true, 0, 0, 1767847369903, 1767847370274, 8, 0, null, List(0, 0), null, 3, 3, 0, 0, null)

### Deep Clone vs Shallow Clone (Delta Table)

**Deep Clone**
- Copies **metadata + actual data files**
- Creates a **fully independent table**
- Changes in source table do **not affect** cloned table
- Requires **more storage**

**Shallow Clone**
- Copies **only metadata**
- Data files are **shared** with source table
- Uses **less storage**
- Faster than deep clone


```


In [0]:
%sql
create table man_cata.man_schema.deepclonetable
deep clone man_cata.man_schema.deltatable;

In [0]:
%sql
-- if u update the delta table it will not affect the deep copu table
select * from man_cata.man_schema.deltatable;


id name city 1 aa toruno 2 bb londom 3 cc sydney

In [0]:
%sql

describe history man_cata.man_schema.deepclonetable;

version timestamp userId userName operation operationParameters job notebook clusterId readVersion isolationLevel isBlindAppend operationMetrics userMetadata engineInfo 0 2026-01-08T04:47:24.000Z 142155304183077 yashthunder12345@gmail.com CLONE Map(source -> man_cata.man_schema.deltatable, sourceVersion -> 5, isShallow -> false) null List(2196879026769418) 0108-041546-i91px7bt-v2n -1 Serializable false Map(removedFilesSize -> 0, numRemovedFiles -> 0, sourceTableSize -> 1000, numCopiedFiles -> 1, numDeletionVectorsAdded -> 0, numDeletionVectorsRemoved -> 0, copiedFilesSize -> 1000, sourceNumOfFiles -> 1) null Databricks-Runtime/17.3.x-photon-scala2.13

In [0]:
%sql

describe extended man_cata.man_schema.deepclonetable;

col_name data_type comment id int null name string null city string null # Delta Statistics Columns Column Names id, name, city Column Selection Method first-32 # Detailed Table Information Catalog man_cata Database man_schema Table deepclonetable Created Time Thu Jan 08 04:47:26 UTC 2026 Last Access UNKNOWN Created By Spark Type MANAGED Location abfss://metadatacontainer@supermanstorage.dfs.core.windows.net/563548be-b032-4de5-a52c-46e654a60590/tables/cd947665-8d09-44a2-bc94-f79dae9a8bfd Provider delta Owner yashthunder12345@gmail.com Is_managed_location true Predictive Optimization ENABLE (inherited from METASTORE supermetastore) Table Properties [delta.enableDeletionVectors=false,delta.feature.appendOnly=supported,delta.feature.deletionVectors=supported,delta.feature.invariants=supported,delta.minReaderVersion=3,delta.minWriterVersion=7,delta.writePartitionColumnsToParquet=true]


### shallow clone

In [0]:
%sql
-- it only copy maanaged table
create table man_cata.man_schema.shallowtable
shallow clone man_cata.man_schema.man_table;

In [0]:
%sql

describe extended man_cata.man_schema.shallowtable;

col_name data_type comment id int null name varchar(20) null # Detailed Table Information Catalog man_cata Database man_schema Table shallowtable Created Time Thu Jan 08 05:11:45 UTC 2026 Last Access UNKNOWN Created By Spark Type MANAGED Location abfss://metadatacontainer@supermanstorage.dfs.core.windows.net/563548be-b032-4de5-a52c-46e654a60590/tables/92f25819-b3ca-4318-9f01-47dc9f23b6a0 Provider delta Owner yashthunder12345@gmail.com Predictive Optimization ENABLE (inherited from METASTORE supermetastore) Table Properties [delta.enableDeletionVectors=true,delta.enableRowTracking=true,delta.feature.appendOnly=supported,delta.feature.deletionVectors=supported,delta.feature.domainMetadata=supported,delta.feature.invariants=supported,delta.feature.rowTracking=supported,delta.minReaderVersion=3,delta.minWriterVersion=7,delta.rowTracking.materializedRowCommitVersionColumnName=_row-commit-version-col-8280e6a5-70df-4fdc-b150-29b714f880ba,delta.rowTracking.materializedRowIdColumnName=_row-id-col-a3d6e191-c039-4ec7-8d1c-04f0444d6760,delta.writePartitionColumnsToParquet=true]


### Autoloader- Incremental loading

Streaming dataframe

In [0]:
df=spark.readStream.format("cloudFiles")\
  .option("cloudFiles.format","parquet")\
  .option("cloudFiles.schemaLocation","abfss://mycontainer@supermanstorage.dfs.core.windows.net/autosink/check")\
    .load("abfss://mycontainer@supermanstorage.dfs.core.windows.net/autosource")
    

In [0]:
df.writeStream \
  .format("parquet") \
  .option(
      "checkpointLocation",
      "abfss://mycontainer@supermanstorage.dfs.core.windows.net/autosink/check"
  ) \
  .trigger(processingTime="10 seconds") \
  .start(
      "abfss://mycontainer@supermanstorage.dfs.core.windows.net/autosink/data"
  )
